In [1]:
import pandas as pd
import csv
import numpy as np
from time import time
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.metrics import classification_report
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import StratifiedKFold

import matplotlib.pyplot as plt

In [2]:
data_train = pd.read_csv('train.csv')
data_test = pd.read_csv('test.csv')

In [3]:
data_train.shape
data_test


Sample ID  Feature_1  Feature_2  Feature_3  Feature_4  Feature_5  \
0             1   0.036550   0.641572  -0.519057   0.460712   0.570700   
1             2  -1.004027   0.534250  -0.259404   0.310052   0.755525   
2             3  -1.147219   0.334078  -0.389740  -0.508234   0.184723   
3             4  -0.506680  -1.361191  -0.576784   0.064672  -0.049516   
4             5  -1.546926   0.966659   0.460473   0.139549  -0.777357   
...         ...        ...        ...        ...        ...        ...   
1995       1996  -1.582811   0.864609   0.612178   0.358372  -1.142419   
1996       1997   1.744843   0.623868  -0.469064   1.619294  -0.944036   
1997       1998  -1.745249   0.983623   0.502273   0.282896  -0.758385   
1998       1999  -1.235580  -0.180367   0.232004  -1.738035   0.262606   
1999       2000   0.295303   0.586335  -1.943268   0.487705  -0.199133   

      Feature_6  Feature_7  Feature_8  Feature_9  ...  Feature_16  Feature_17  \
0      0.222309   0.087710  -0.318400  -1.973283  ...   -1.049741   -1.672266   
1     -0.267865   0.803048   0.824546  -0.017057  ...   -0.377550    0.455779   
2      1.956903   1.366785   0.906050  -0.138883  ...    0.316459   -1.694966   
3     -0.111892   0.502428  -0.332201  -1.203807  ...   -0.187222   -1.211090   
4     -0.015657   1.188006   1.035923  -0.326310  ...    0.404783   -0.386269   
...         ...        ...        ...        ...  ...         ...         ...   
1995   0.675760   0.986953   0.802516  -0.294720  ...    0.592820   -0.717194   
1996  -0.744784   0.073100   0.934007  -1.300712  ...   -1.452097    0.099856   
1997  -0.294727   0.434684   0.807753   0.797022  ...    0.058739   -0.481010   
1998  -0.283989   1.539323  -0.661559   1.040505  ...    0.455763   -1.096604   
1999  -1.727402  -0.849607   0.619744   0.122939  ...    1.857233   -0.413658   

      Feature_18  Feature_19  Feature_20  Feature_21  Feature_22  Feature_23  \
0       1.059074    0.206516    0.792531    0.844650   -0.784680    0.937180   
1      -1.574711   -0.374946    1.361794   -0.062464    1.167719    1.231902   
2      -0.511869    0.123451   -1.174886    0.341067    0.196467   -0.686200   
3      -1.062384   -0.162851    1.043950    0.482891   -0.582693   -0.358026   
4      -0.727555    0.454785   -1.020171    0.171097    0.059959    0.638194   
...          ...         ...         ...         ...         ...         ...   
1995   -0.008238    0.278941   -1.016759    0.229739    1.066610    0.164713   
1996    0.092569    0.828947   -0.176099    0.073565    0.988890   -1.063531   
1997   -0.342823    0.254859    0.080882    0.159286    0.074396    0.510993   
1998    0.034090    0.154824    0.432887    1.724974   -0.830066    1.066209   
1999   -2.137722    0.697366    1.741294    1.250204   -0.688708   -1.682783   

      Feature_24  Feature_25  
0       0.043382    0.583525  
1       0.462682    0.697925  
2       0.509537    0.993518  
3      -1.188908   -0.221639  
4       1.095800   -0.612439  
...          ...         ...  
1995    0.368491   -1.329390  
1996    0.467692   -0.822960  
1997    0.319498   -0.359889  
1998    1.013639   -0.291611  
1999    1.949977    1.197657  

[2000 rows x 26 columns]

#train 2000 instances sample from 8000 by 25 training data set

In [4]:
features_train = np.array(data_train.iloc[:6000,1:26])
labels_train = np.array(data_train.iloc[:6000, 26:])
features_test = np.array(data_train.iloc[6000:,1:26])
labels_test = np.array(data_train.iloc[6000: ,26:])
features_test1=np.array(data_test.iloc[:,1:])

In [5]:
features_test1

array([[ 0.0365502 ,  0.64157185, -0.51905704, ...,  0.93717975,
         0.04338224,  0.58352457],
       [-1.00402684,  0.53424971, -0.25940372, ...,  1.23190188,
         0.46268162,  0.69792463],
       [-1.14721948,  0.33407755, -0.38973985, ..., -0.68620045,
         0.50953749,  0.99351821],
       ...,
       [-1.74524935,  0.98362278,  0.50227314, ...,  0.51099299,
         0.31949771, -0.35988901],
       [-1.23558046, -0.18036654,  0.23200449, ...,  1.06620871,
         1.01363871, -0.29161062],
       [ 0.29530338,  0.58633481, -1.9432677 , ..., -1.68278298,
         1.94997667,  1.19765727]])

In [6]:
kf = StratifiedKFold(n_splits=3)
C_range = 2. ** np.arange(-5, 15)
gamma_range = 2. ** np.arange(-15, 3)
degree_range = np.arange(1,20)

In [7]:
C_range.shape

(20,)

In [8]:
coef0_range =np.arange(-2,2)

kernel = ['linear']

param_grid = dict(gamma=[6.103515625e-05], C=[0.0625],max_iter= [248])
grid = GridSearchCV(SVC(), param_grid=param_grid, cv=StratifiedKFold(n_splits=3))
t0= time()
grid.fit(features_train,labels_train.ravel())
pred = grid.predict(features_test1)
print(pred)

C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=248).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=248).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=248).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation

[8 9 8 ... 1 9 8]


In [9]:
pred.shape

(2000,)

In [10]:
y=pd.DataFrame({'Sample ID':data_test['Sample ID'],'class':pred})
y.to_csv('2021AMA2095_RESULT_1.csv')
print("")
print('final class predicted on test data')
print("")
print(pd.DataFrame(y))


final class predicted on test data

      Sample ID  class
0             1      8
1             2      9
2             3      8
3             4      9
4             5      8
...         ...    ...
1995       1996      1
1996       1997      0
1997       1998      1
1998       1999      9
1999       2000      8

[2000 rows x 2 columns]


polykernel

In [11]:
print ('fitting time',time()-t0)
print (grid.best_estimator_)
print (grid.score(features_train,labels_train.ravel()))
print (grid.score(features_test,labels_test.ravel()))



fitting time 10.738650560379028
SVC(C=0.0625, gamma=6.103515625e-05, max_iter=248)
0.5513333333333333
0.5265


In [12]:
i=0


print (1)
train_error = []
val_error = []


for c in C_range:
    clf = SVC(C=c, kernel='linear', max_iter=1000)

    train_score = 0
    val_score = 0
    for train_index, val_index in kf.split(features_train, labels_train.ravel()):
        X_train, X_val = features_train[train_index], features_train[val_index]
        Y_train, Y_val = labels_train[train_index], labels_train[val_index]

        clf.fit(X_train, Y_train.ravel())
        pred=clf.predict(features_test1)
        train_score = train_score + clf.score(X_train, Y_train.ravel())
        # print log_loss(Y_train.ravel(),clf.predict(X_train)),'train'
        val_score = val_score + clf.score(X_val, Y_val.ravel())

    i = i + 1
    print (i)

    train_error = train_error + [1 - (train_score / 4)]
    val_error = val_error + [1 - (val_score / 4)]

print (train_error, 'linear')
print (val_error, 'linear')
plt.plot(C_range, train_error, label='linear')
plt.plot(C_range, val_error)
plt.show()

1


C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=1000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(


1


C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=1000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=1000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=1000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(


2


...

18


C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=1000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=1000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=1000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(


19


C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=1000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=1000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=1000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(


20
[0.3096875000000001, 0.30818750000000006, 0.3046875, 0.301875, 0.29925, 0.29637500000000006, 0.2940625, 0.30818749999999995, 0.358, 0.3878125, 0.406625, 0.40874999999999995, 0.4088125, 0.4088125, 0.4088125, 0.4088125, 0.4088125, 0.4088125, 0.4088125, 0.4088125] linear
[0.317125, 0.3185, 0.31775, 0.319125, 0.3185, 0.31962500000000005, 0.32162500000000005, 0.33787500000000004, 0.38612500000000005, 0.40812499999999996, 0.423875, 0.4275, 0.42737499999999995, 0.42737499999999995, 0.42737499999999995, 0.42737499999999995, 0.42737499999999995, 0.42737499999999995, 0.42737499999999995, 0.42737499999999995] linear


In [13]:
print(pred)

[6 8 1 ... 1 3 3]


In [14]:
y=pd.DataFrame({'Sample ID':data_test['Sample ID'],'Class':pred})
y.to_csv('2021AMA2095_RESULT_2.csv')
print("")
print('final class predicted on test data')
print("")
print(pd.DataFrame(y))


final class predicted on test data

      Sample ID  Class
0             1      6
1             2      8
2             3      1
3             4      7
4             5      1
...         ...    ...
1995       1996      1
1996       1997      0
1997       1998      1
1998       1999      3
1999       2000      3

[2000 rows x 2 columns]


In [ ]:


svm = SVC(kernel='rbf', random_state=1, gamma=0.1, C=0.02,degree=3)

svm.fit(features_train,labels_train.ravel())


SVC(C=0.02, gamma=0.1, random_state=1)

In [19]:
###RBF ker

param_grid = dict(gamma=gamma_range, C=C_range,max_iter= [100],kernel=['rbf'])

grid = GridSearchCV(SVC(), param_grid=param_grid, cv=StratifiedKFold(n_splits=3))
t0= time()
grid.fit(features_train,labels_train.ravel())


C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation

GridSearchCV(cv=StratifiedKFold(n_splits=3, random_state=None, shuffle=False),
             estimator=SVC(),
             param_grid={'C': array([3.1250e-02, 6.2500e-02, 1.2500e-01, 2.5000e-01, 5.0000e-01,
       1.0000e+00, 2.0000e+00, 4.0000e+00, 8.0000e+00, 1.6000e+01,
       3.2000e+01, 6.4000e+01, 1.2800e+02, 2.5600e+02, 5.1200e+02,
       1.0240e+03, 2.0480e+03, 4.0960e+03, 8.1920e+03, 1.6384e+04]),
                         'gamma': array([3.05175781e-05, 6.10351562e-05, 1.22070312e-04, 2.44140625e-04,
       4.88281250e-04, 9.76562500e-04, 1.95312500e-03, 3.90625000e-03,
       7.81250000e-03, 1.56250000e-02, 3.12500000e-02, 6.25000000e-02,
       1.25000000e-01, 2.50000000e-01, 5.00000000e-01, 1.00000000e+00,
       2.00000000e+00, 4.00000000e+00]),
                         'kernel': ['rbf'], 'max_iter': [100]})

In [20]:
print ('fitting time',time()-t0)
print (grid.best_estimator_)
print (grid.score(features_train,labels_train.ravel()))
print (grid.score(features_test,labels_test.ravel()))

fitting time 2156.466334581375
SVC(C=32.0, gamma=0.0625, max_iter=100)
1.0
0.9665


In [21]:
pred_RBF=grid.predict(features_test1)
print(pred_RBF)

[8 7 1 ... 1 9 3]


In [22]:
y=pd.DataFrame({'Sample ID':data_test['Sample ID'],'Class':pred_RBF})
y.to_csv('2021AMA2095_RESULT_8.csv')
print("")
print('final class predicted on test data')
print("")
print(pd.DataFrame(y))


final class predicted on test data

      Sample ID  Class
0             1      8
1             2      7
2             3      1
3             4      7
4             5      1
...         ...    ...
1995       1996      1
1996       1997      0
1997       1998      1
1998       1999      9
1999       2000      3

[2000 rows x 2 columns]


In [23]:
score_dict = grid.cv_results_

# We extract just the scores
scores = [x[1] for x in score_dict]
scores = np.array(scores)

In [24]:
scores

array(['e', 't', 'e', 't', 'a', 'a', 'a', 'a', 'a', 'p', 'p', 'p', 'e',
       't', 'a'], dtype='<U1')

In [26]:
param_grid = dict(degree=degree_range, C=C_range,max_iter= [10],gamma = gamma_range, coef0= coef0_range,kernel=['poly'])

grid = GridSearchCV(SVC(), param_grid=param_grid, cv=StratifiedKFold(n_splits=3))
t0 = time()
grid.fit(features_train,labels_train.ravel())

print ('###PolyKernal###')
print ("fitting time",time()-t0)
print (grid.best_estimator_)
print (grid.score(features_test,labels_test.ravel()))


C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=10).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=10).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\svm\_base.py:301: ConvergenceWarning: Solver terminated early (max_iter=10).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
C:\Users\acer\AppData\Local\Packages\PythonSoftwareFoundation.Py

In [ ]:
print ('fitting time',time()-t0)
print (grid.best_estimator_)
print (grid.score(features_train,labels_train.ravel()))
print (grid.score(features_test,labels_test.ravel()))

In [ ]:

score_dict = grid.grid_scores_

# We extract just the scores
scores = [x[1] for x in score_dict]
scores = np.array(scores).reshape(len(C_range), len(degree_range))